In [1]:
import sys
sys.path.append("../scripts/")
from robot import *
from scipy.stats import multivariate_normal

In [2]:
class Particle:
    def __init__(self, init_pose):
        self.pose = init_pose

    def motion_update(self, nu, omega, time, noise_rate_pdf):
        ns = noise_rate_pdf.rvs() # 順にnn, no, on, oo
        # 速度に雑音を加える
        noised_nu = nu + ns[0]*math.sqrt(abs(nu)/time) + ns[1]*math.sqrt(abs(omega)/time)
        # 角速度に雑音を加える
        noised_omega = omega + ns[2]*math.sqrt(abs(nu)/time) + ns[3]*math.sqrt(abs(omega)/time)
        # 姿勢を更新する
        self.pose = IdealRobot.state_transition(noised_nu, noised_omega, time, self.pose)

In [3]:
class Mcl:
    def __init__(self, init_pose, num, motion_noise_stds):
        self.particles = [Particle(init_pose) for i in range(num)]

        v = motion_noise_stds # 標準偏差σabに対応

        # ４次元のガウス分布のオブジェクトを作る
        c = np.diag([v["nn"]**2, v["no"]**2, v["on"]**2, v["oo"]**2]) # 対角行列を作って返す
        self.motion_noise_rate_pdf = multivariate_normal(cov=c)

    def motion_update(self, nu, omega, time):
        for p in self.particles: p.motion_update(nu, omega, time, self.motion_noise_rate_pdf)
                                                             
    def draw(self, ax, elems):
        # 全パーティクルのX座標、Y座標をリスト化する
        xs = [p.pose[0] for p in self.particles]
        ys = [p.pose[1] for p in self.particles]

        # パーティクルの向きを描画するために、向きをベクトルで表したときのX座標、Y座標成分のリストを作る
        vxs = [math.cos(p.pose[2]) for p in self.particles]
        vys = [math.sin(p.pose[2]) for p in self.particles]
        
        elems.append(ax.quiver(xs, ys, vxs, vys, color="blue", alpha=0.5))

In [4]:
class EstimationAgent(Agent):
    def __init__(self, time_interval, nu, omega, estimator):
        super().__init__(nu, omega)
        self.estimator = estimator
        self.time_interval = time_interval

        self.prev_nu = 0.0
        self.prev_omega = 0.0

    def decision(self, observation=None):
        # 一つ前の制御指令値でパーティクルの姿勢を更新する
        self.estimator.motion_update(self.prev_nu, self.prev_omega, self.time_interval)
        self.prev_nu, self.prev_omega = self.nu, self.omega
        return self.nu, self.omega
    
    def draw(self, ax, elems):
        self.estimator.draw(ax, elems)

In [5]:
initial_pose = np.array([0, 0, 0]).T
estimator = Mcl(initial_pose, 100, motion_noise_stds={"nn":0.01, "no":0.02, "on":0.03, "oo":0.04})
a = EstimationAgent(0.1, 0.2, 10.0/180*math.pi, estimator)
estimator.motion_update(0.2, 10.0/180*math.pi, 0.1)
for p in estimator.particles:
    print(p.pose)

[1.76457737e-02 5.25775331e-05 5.95920342e-03]
[0.02372395 0.00014282 0.01204026]
[0.0177265  0.00019775 0.02230995]
[0.02135824 0.00014312 0.01340126]
[0.0142406  0.00014438 0.0202768 ]
[1.58874640e-02 1.90746491e-05 2.40121897e-03]
[0.02295572 0.00020616 0.01796148]
[0.02165681 0.00015483 0.014298  ]
[0.01892758 0.00015459 0.01633474]
[2.00738408e-02 9.36087089e-05 9.32636970e-03]
[0.01761697 0.00019977 0.0226786 ]
[0.017255   0.00016607 0.01924815]
[0.02380887 0.00022887 0.01922467]
[0.01929365 0.00014264 0.01478617]
[0.01909778 0.00025943 0.02716678]
[0.01818886 0.00021009 0.02309985]
[0.01680725 0.0001961  0.02333433]
[0.02485869 0.00011598 0.00933079]
[0.02004151 0.00023391 0.02334136]
[0.02098368 0.0001936  0.01845156]
[0.01527896 0.00015583 0.02039768]
[0.01593539 0.00019471 0.02443578]
[0.01899616 0.00010915 0.01149182]
[0.01487948 0.00018008 0.02420443]
[0.01895243 0.00019402 0.02047418]
[0.01693601 0.00013213 0.01560298]
[0.02394338 0.00019782 0.01652401]
[0.01907046 0.00012

In [6]:
motion_noise_stds = {"nn": 0.01, "no": 0.02, "on": 0.03, "oo": 0.04}
time_interval = 0.1
world = World(30, time_interval)

initial_pose = np.array([0, 0, 0]).T
estimator = Mcl(initial_pose, 100, motion_noise_stds)
circling = EstimationAgent(time_interval, 0.2, 10.0/180*math.pi, estimator)
r = Robot(initial_pose, sensor=None, agent=circling, color="red")
world.append(r)

world.draw()